In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px

# Load your dataset
df = pd.read_csv('vehicles_us.csv')
# Previewing Data
# What types of data?
df.info()
print()
# First 5 rows - like meeting someone for the first time
print(df.head(10))
print()
print(df.describe())
print()
print(df.isnull().sum())


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB

   price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      for

In [2]:
# Fixing Data
# Changing columns to Integer64 dtype
df['model_year'] = df['model_year'].astype("Int64")
df['odometer'] = df['odometer'].astype("Int64")
# Changing 'is_4wd' column to Integer64 dtype and filled NaN with 0
df['is_4wd'] = df['is_4wd'].fillna(0).astype("Int64")
# Converting 'price' and 'days_listed' column to Int64 dtype to keep consistency
df['price'] = df['price'].astype("Int64")
df['days_listed'] = df['days_listed'].astype("Int64")

# Changing columns to category dtype
df['model'] = df['model'].astype('category')
df['condition'] = df['condition'].astype('category')
# Filling NaN values in 'cylinders' with 'unknown'
df['cylinders'] = df['cylinders'].fillna(0).astype(int)
df['cylinders'] = df['cylinders'].replace(0, 'unknown').astype('category')
df['fuel'] = df['fuel'].astype('category')
df['transmission'] = df['transmission'].astype('category')
df['type'] = df['type'].astype('category')
df['paint_color'] = df['paint_color'].astype('category')
# Filling NaN values in 'paint_color' with 'unknown'
df['paint_color'] = df['paint_color'].cat.add_categories(['unknown']).fillna('unknown')

# Converting 'date_posted' column to datetime dtype
df['date_posted'] = pd.to_datetime(df['date_posted'], errors='coerce')
# Droping rows with null 'model_year' or 'odometer' values
df = df.dropna(subset=['model_year', 'odometer'])
df.info()
print()
print(df.isnull().sum())
print()
print(df.head())


<class 'pandas.core.frame.DataFrame'>
Index: 40563 entries, 0 to 51523
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   price         40563 non-null  Int64         
 1   model_year    40563 non-null  Int64         
 2   model         40563 non-null  category      
 3   condition     40563 non-null  category      
 4   cylinders     40563 non-null  category      
 5   fuel          40563 non-null  category      
 6   odometer      40563 non-null  Int64         
 7   transmission  40563 non-null  category      
 8   type          40563 non-null  category      
 9   paint_color   40563 non-null  category      
 10  is_4wd        40563 non-null  Int64         
 11  date_posted   40563 non-null  datetime64[ns]
 12  days_listed   40563 non-null  Int64         
dtypes: Int64(5), category(7), datetime64[ns](1)
memory usage: 2.6 MB

price           0
model_year      0
model           0
condition       0
cyl

In [3]:
# Enriching data
# Extracting the make from the 'model' column and assigning them to its own 'make' column
# Keeping 'model' column as is to preserve the full model name
df['make'] = df['model'].str.split().str[0]
df['make'] = df['make'].astype('category')
# Rearranging columns in the DataFrame
df = df[['price', 'model_year', 'make', 'model', 'condition', 'cylinders', 'fuel', 'odometer', 'transmission', 'type', 'paint_color', 'is_4wd', 'date_posted', 'days_listed']]
# Printing the number of rows before dropping outliers
print("Removing obvious outliers in the data for listing prices below $1,000 and above $200,000.")
print(f"- Number of rows before dropping outliers: {len(df)}")
# Droping rows with price less than $1000 and greater than $200,000 to remove obvious outliers in the data
df = df[(df['price'] >= 1000) & (df['price'] <= 200000)]
# Printing the number of rows after dropping outliers
print(f"- Number of rows after dropping outliers: {len(df)}")
print()
df.info()
print()
print(df.head())

Removing obvious outliers in the data for listing prices below $1,000 and above $200,000.
- Number of rows before dropping outliers: 40563
- Number of rows after dropping outliers: 39457

<class 'pandas.core.frame.DataFrame'>
Index: 39457 entries, 0 to 51523
Data columns (total 14 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   price         39457 non-null  Int64         
 1   model_year    39457 non-null  Int64         
 2   make          39457 non-null  category      
 3   model         39457 non-null  category      
 4   condition     39457 non-null  category      
 5   cylinders     39457 non-null  category      
 6   fuel          39457 non-null  category      
 7   odometer      39457 non-null  Int64         
 8   transmission  39457 non-null  category      
 9   type          39457 non-null  category      
 10  paint_color   39457 non-null  category      
 11  is_4wd        39457 non-null  Int64         
 12  dat

In [4]:
# Grouping vehicle listings by date and calculating the count and average days listed
listing_by_date = df.groupby(
    [df['date_posted'].dt.year, df['date_posted'].dt.month]
).agg(
    listings=('type', 'size'),
    avg_days_listed=('days_listed', 'mean')
)
listing_by_date['avg_days_listed'] = listing_by_date['avg_days_listed'].round(1)
print(listing_by_date)
print()
# Calculating the average number of listings per month and the average number of days listed
avg_listings_per_month = listing_by_date['listings'].mean()
avg_days_listed = listing_by_date['avg_days_listed'].mean()
print(f"The average number of listings per month is: {avg_listings_per_month:.1f}")
print(f"The average number of days listed per month is: {avg_days_listed:.1f}")

                         listings  avg_days_listed
date_posted date_posted                           
2018        5                3413             40.0
            6                3245             39.9
            7                3401             39.7
            8                3456             39.1
            9                3424             40.2
            10               3573             38.8
            11               3329             39.8
            12               3476             38.8
2019        1                3388             39.4
            2                3042             40.4
            3                3526             40.3
            4                2184             39.9

The average number of listings per month is: 3288.1
The average number of days listed per month is: 39.7


In [ ]:
# Grouping vehicles by type and calculating the mean price, odometer reading, and days listed
vehicles_by_type = df.groupby('type', observed=True).agg(
    count=('type', 'size'),
    avg_price=('price', 'mean'),
    avg_odometer=('odometer', 'mean'),
    percent_of_4wd=('is_4wd', lambda x: (x > 0).mean() * 100),
    avg_days_listed=('days_listed', 'mean'),
).reset_index()
# Rounding the average price, odometer, and days listed to 1 decimal place
vehicles_by_type[['avg_price', 'avg_odometer', 'percent_of_4wd', 'avg_days_listed']] = vehicles_by_type[['avg_price', 'avg_odometer', 'percent_of_4wd', 'avg_days_listed']].round(1)
print(f"Vehicle Listings Summary by Type:\n{vehicles_by_type.to_string(index=False)}")
print()

# Getting unique types, sort them case-insensitively in order for the types to appear in alphabetical order
sorted_types = sorted(df['type'].cat.categories, key=lambda x: x.lower())
df['type'] = df['type'].cat.reorder_categories(sorted_types, ordered=True)

# Visualizing the vehicle prices by type
px.box(
    df,
    x='type',
    y='price',
    labels={'type': "Vehicle Type", 'price': "Price ($)"},
    title='Vehicle Prices by Type'
).show()
# Old plt graph
#df.boxplot(column='price', by='type', rot=45)
#plt.title('Vehicle Prices by Type')
#plt.suptitle('')
#plt.xlabel('Vehicle Type')
#plt.ylabel('Price ($)')
#plt.show()
print("Analysis: Trucks have the widest spread in prices, indicating a broad range of models and conditions."
      "\nMany vehicle price outliers begin to appear around $60,000 to $75,000.")
print()

# Visualizing the vehicle model years by type
px.box(
    df,
    x='type',
    y='model_year',
    labels={'type': "Vehicle Type", 'model_year': "Model Year"},
    title='Vehicle Model Years by Type'
).show()
# Old plt graph
#df.boxplot(column='model_year', by='type', rot=45)
#plt.title('Vehicle Model Years by Type')
#plt.suptitle('')
#plt.xlabel('Vehicle Type')
#plt.ylabel('Model Year')
#plt.show()
print("Analysis: Vehicle model years outliers are scattered across many vehicle types, with most coming from vehicles older than 1980.")
print()

# Visualizing the vehicle odometer readings by type
px.box(
    df,
    x='type',
    y='odometer',
    labels={'type': "Vehicle Type", 'odometer': "Miles"},
    title='Vehicle Miles by Type'
).show()
# Old plt graph
#df.boxplot(column='odometer', by='type', rot=45)
#plt.title('Vehicle Miles by Type')
#plt.suptitle('')
#plt.xlabel('Vehicle Type')
#plt.ylabel('Miles')
#plt.show()
print("Analysis: The majority of vehicles have odometer readings below 200,000 miles, and outliers begin to appear above 400,000 miles."
      "\nThe 'other' vehicle type is an outlier in all three categories and is not beneficial to the overall analysis."
      "\nWith only 202 listings, it is not a significant portion of the dataset and can be safely excluded.")

Vehicle Listings Summary by Type:
       type  count  avg_price  avg_odometer  percent_of_4wd  avg_days_listed
        bus     23    16620.3      114198.2             0.0             45.0
convertible    349    15136.1       86934.2             9.2             39.1
      coupe   1767    14955.4       79107.9             0.3             39.6
  hatchback    816     7036.3      111337.7            14.0             40.8
   mini-van    915     8332.6      126987.4             3.2             39.9
    offroad    177    14052.1      121814.7            96.0             39.9
      other    202    11026.6      109775.1            49.5             38.0
     pickup   5440    16254.8      120072.8            72.2             39.4
      sedan   9196     7222.4      108320.6             3.8             39.4
        SUV   9424    11617.8      119713.3            71.6             40.0
      truck   9511    17188.7      124971.4            75.3             39.5
        van    446     9443.7      125034.

Analysis: Trucks have the widest spread in prices, indicating a broad range of models and conditions.
Many vehicle price outliers begin to appear around $60,000 to $75,000.



Analysis: Vehicle model years outliers are scattered across many vehicle types, with most coming from vehicles older than 1980.



Analysis: The majority of vehicles have odometer readings below 200,000 miles, and outliers begin to appear above 400,000 miles.
The 'other' vehicle type is an outlier in all three categories and is not beneficial to the overall analysis.
With only 202 listings, it is not a significant portion of the dataset and can be safely excluded.


In [6]:
# Grouping vehicles by make and calculating the mean price, odometer reading, and days listed
vehicles_by_make = df.groupby('make', observed=True).agg(
    count=('make', 'size'),
    avg_price=('price', 'mean'),
    avg_odometer=('odometer', 'mean'),
    percent_of_4wd=('is_4wd', lambda x: (x > 0).mean() * 100),
    avg_days_listed=('days_listed', 'mean'),
).reset_index()
# Rounding the average price, odometer, and days listed to 1 decimal place
vehicles_by_make[['avg_price', 'avg_odometer', 'percent_of_4wd', 'avg_days_listed']] = vehicles_by_make[['avg_price', 'avg_odometer', 'percent_of_4wd', 'avg_days_listed']].round(1)
print(f"Vehicle Listings Summary by Make:\n{vehicles_by_make.to_string(index=False)}")
print()

# Visualizing the vehicle prices by make
px.box(
    df,
    x='make',
    y='price',
    labels={'make': "Vehicle Make", 'price': "Price ($)"},
    title='Vehicle Prices by Make'
).show()
# Old plt graph
#df.boxplot(column='price', by='make', rot=45)
#plt.title('Vehicle Prices by Make')
#plt.suptitle('')
#plt.xlabel('Vehicle Make')
#plt.ylabel('Price ($)')
#plt.show()
print("Analysis: Many vehicle makes display outliers for vehicles priced above $75,000"
      "\nThese findings of consistent outliers beyond $75,000 across vehicle types and vehicle makes allow the analysis to safely exclude vehicle listings over $75,000.")

# Visualizing the vehicle model years by make
px.box(
    df,
    x='make',
    y='model_year',
    labels={'make': "Vehicle Make", 'model_year': "Model Year"},
    title='Vehicle Model Years by Make'
).show()
# Old plt graph
#df.boxplot(column='model_year', by='make', rot=45)
#plt.title('Vehicle Model Years by Make')
#plt.suptitle('')
#plt.xlabel('Vehicle Make')
#plt.ylabel('Model Year')
#plt.show()
print("Analysis: Majority of model year outliers begin to show in vehicles older than 1980"
      "\nThese findings of consistent outliers from vehicles older than 1970 allow the analysis to safely exclude listings of vehicles older than 1970.")

# Visualizing the vehicle odometer readings by make
px.box(
    df,
    x='make',
    y='odometer',
    labels={'make': "Vehicle Make", 'odometer': "Miles"},
    title='Vehicle Miles by Make'
).show()
# Old plt graph
#df.boxplot(column='odometer', by='make', rot=45)
#plt.title('Vehicle Miles by Make')
#plt.suptitle('')
#plt.xlabel('Vehicle Make')
#plt.ylabel('Miles')
#plt.show()
print("Analysis: Many vehicle makes show outliers scattered across the odometer readings, with most outliers beginning to show above 400,000 miles."
      "\nThese findings of consistent outliers from vehicles with odometer readings above 400,000 miles allow the analysis to safely exclude listings of vehicles with odometer readings above 400,000 miles.")

Vehicle Listings Summary by Make:
      make  count  avg_price  avg_odometer  percent_of_4wd  avg_days_listed
     acura    190     6327.4      144082.5             8.4             39.4
       bmw    210    10808.8      112532.3            90.5             42.4
     buick    217    11582.4      112857.6            48.8             39.9
  cadillac    242    18187.5      120804.4            78.9             41.4
 chevrolet   8225    14784.9      112451.6            53.6             39.7
  chrysler    646     8426.9      108699.9             7.3             38.3
     dodge    912     8722.9      116633.1            15.6             39.8
      ford   9750    12975.2      117735.3            52.4             39.7
       gmc   1821    15958.5      127789.4            75.1             40.9
     honda   2683     7561.1      126544.5            22.6             39.4
   hyundai    909     7343.6      104272.2            11.6             38.5
      jeep   2463    13507.2      111493.2            

Analysis: Many vehicle makes display outliers for vehicles priced above $75,000
These findings of consistent outliers beyond $75,000 across vehicle types and vehicle makes allow the analysis to safely exclude vehicle listings over $75,000.


Analysis: Majority of model year outliers begin to show in vehicles older than 1980
These findings of consistent outliers from vehicles older than 1970 allow the analysis to safely exclude listings of vehicles older than 1970.


Analysis: Many vehicle makes show outliers scattered across the odometer readings, with most outliers beginning to show above 400,000 miles.
These findings of consistent outliers from vehicles with odometer readings above 400,000 miles allow the analysis to safely exclude listings of vehicles with odometer readings above 400,000 miles.


In [ ]:
# Creating a new DF with 'other' vehicle type removed,
# and only including vehicles priced up to $75,000, model year 1980 and newer and miles 400,000 and under
df_75k = df
df_75k = df_75k[df_75k['price'] <= 75000]
df_75k = df_75k[df_75k['model_year'] >= 1980]
df_75k = df_75k[df_75k['odometer'] <= 400000]
# Dropping 'other' vehicle type
df_75k = df_75k[df_75k['type'] != 'other']
print(f"Listings of Vehicles from 1980 or newer with 400k miles or less, priced $75,000 or under:\n{df_75k.head()}")
print()
print(f"Number of vehicle listings after filtering outliers: {len(df_75k)}")
print()

# Visualizing the relationship between miles, price and model year
px.scatter(
    df_75k,
    x='odometer',
    y='price',
    labels={'odometer': "Miles", 'price': "Price ($)"},
    title='Vehicle Price vs Miles ($75k and under)'
).show()
# Old plt graph
#df_75k.plot(kind='scatter', x='odometer', y='price', alpha=0.3)
#plt.xlabel('Miles')
#plt.ylabel('Price ($)')
#plt.title('Odometer vs. Price')
#plt.show()
print("Miles have a negative correlation with price, indicating that as the odometer reading increases, the price tends to decrease.")
print()

px.scatter(
    df_75k,
    x='model_year',
    y='price',
    labels={'model_year': "Model Year", 'price': "Price ($)"},
    title='Vehicle Price vs Model Year ($75k and under)'
).show()
# Old plt graph
#df_75k.plot(kind='scatter', x='model_year', y='price', alpha=0.3)
#plt.xlabel('Model Year')
#plt.ylabel('Price ($)')
#plt.title('Model Year vs. Price')
#plt.show()
print("Model year has a positive correlation with price, indicating that newer vehicles tend to be priced higher than older vehicles.")
print()


Listings of Vehicles from 1980 or newer with 400k miles or less, priced $75,000 or under:
   price  model_year      make           model  condition cylinders fuel  \
0   9400        2011       bmw          bmw x5       good         6  gas   
2   5500        2013   hyundai  hyundai sonata   like new         4  gas   
4  14900        2017  chrysler    chrysler 200  excellent         4  gas   
5  14990        2014  chrysler    chrysler 300  excellent         6  gas   
6  12990        2015    toyota    toyota camry  excellent         4  gas   

   odometer transmission   type paint_color  is_4wd date_posted  days_listed  
0    145000    automatic    SUV     unknown       1  2018-06-23           19  
2    110000    automatic  sedan         red       0  2019-02-07           79  
4     80903    automatic  sedan       black       0  2019-04-02           28  
5     57954    automatic  sedan       black       1  2018-06-20           15  
6     79212    automatic  sedan       white       0  2018-

Miles have a negative correlation with price, indicating that as the odometer reading increases, the price tends to decrease.



Model year has a positive correlation with price, indicating that newer vehicles tend to be priced higher than older vehicles.



In [ ]:
# Grouping vehicles $75k and under by type and calculating the mean price, odometer reading, and days listed
vehicles_by_type_75k = df_75k.groupby('type', observed=True).agg(
    count=('type', 'size'),
    avg_price=('price', 'mean'),
    avg_odometer=('odometer', 'mean'),
    percent_of_4wd=('is_4wd', lambda x: (x > 0).mean() * 75),
    avg_days_listed=('days_listed', 'mean'),
).reset_index()
# Rounding the average price, odometer, and days listed to 1 decimal place
vehicles_by_type_75k[['avg_price', 'avg_odometer', 'percent_of_4wd', 'avg_days_listed']] = vehicles_by_type_75k[['avg_price', 'avg_odometer', 'percent_of_4wd', 'avg_days_listed']].round(1)
print(f"Vehicle Listings ($75k and under) Summary by Type:\n{vehicles_by_type_75k.to_string(index=False)}")
print()

# Visualizing the number of vehicle listings by type
px.bar(
    vehicles_by_type_75k,
    x='type',
    y='count',
    labels={'type': "Vehicle Type", 'count': "Listings"},
    title='Vehicle Listings by Type ($75k and under)'
).show()
# Old plt graph
#vehicles_by_type_75k.plot(kind='bar', x='type', y='count', title='Number of Vehicle Listings by Type ($75k and under)')
#plt.xlabel('Vehicle Type')
#plt.legend().set_visible(False)
#plt.show()
# Displaying the top 4 most and least listed vehicle types
top4_most_listed_type_75k = df_75k['type'].value_counts().head(4)
print(f"Top 4 most listed vehicle types ($75k and under):\n{top4_most_listed_type_75k.to_string(header=False)}")
print()
# 'other' type still shows up because it exists as a category in the 'type' column, even if there are 0 rows of that type after filtering.
# When you use value_counts() on a pandas categorical column, it includes all categories by default, even those with zero count.
# To exclude 'other' from the results, you can filter it out explicitly:

top4_least_listed_type_75k = df_75k['type'].value_counts()
top4_least_listed_type_75k = top4_least_listed_type_75k[top4_least_listed_type_75k.index != 'other']
top4_least_listed_type_75k = top4_least_listed_type_75k.tail(4).sort_values(ascending=True)
print(f"Top 4 least listed vehicle types ($75k and under):\n{top4_least_listed_type_75k.to_string(header=False)}")
print()

# Distribution of vehicle prices $75k and under
px.histogram(
    df_75k,
    x='price',
    nbins=40,
    labels={'price': "Price ($)"},
    title='Distribution of Vehicle Prices ($75k and under)'
).update_yaxes(title_text="Listings").show()
# Old plt graph
#df_75k['price'].hist(bins=20,)
#plt.suptitle('Distribution of Vehicle Prices ($75k and under)')
#plt.xlabel('Price ($)')
#plt.ylabel('Frequency')
#plt.show()

# Visualizing the vehicle prices by type
px.box(
    df_75k,
    x='type',
    y='price',
    labels={'type': "Vehicle Type", 'price': "Price ($)"},
    title='Vehicle Prices by Type ($75k and under)'
).show()
# Old plt graph
#df_75k.boxplot(column='price', by='type', rot=45)
#plt.title('Vehicle Prices by Type ($75k and under)')
#plt.suptitle('')
#plt.xlabel('Vehicle Type')
#plt.ylabel('Price ($)')
#plt.show()
# Displaying the top 4 most and least expensive vehicle types
top4_expensive_type_75k = vehicles_by_type_75k.nlargest(4, 'avg_price')
print(f"Top 4 most expensive vehicle types by averge price ($75k and under):\n{top4_expensive_type_75k[['type', 'avg_price']].to_string(index=False, header=False)}")
print()
top4_least_expensive_type_75k = vehicles_by_type_75k.nsmallest(4, 'avg_price')
print(f"Top 4 least expensive vehicle types by average price ($75k and under):\n{top4_least_expensive_type_75k[['type', 'avg_price']].to_string(index=False, header=False)}")
print()

# Displaying the top 4 vehicle types with 4wd
top4_4wd_type_75k = vehicles_by_type_75k.nlargest(4, 'percent_of_4wd')
print(f"Top 4 vehicle types with the highest percentage of 4wd ($75k and under):\n{top4_4wd_type_75k[['type', 'percent_of_4wd']].to_string(index=False, header=False)}")
print()

# Displaying the top 4 vehicle types with the shorted and longest average days listed
top4_shortest_days_listed_type_75k = vehicles_by_type_75k.nsmallest(4, 'avg_days_listed')
print(f"Top 4 vehicle types with the shortest average days listed ($75k and under):\n{top4_shortest_days_listed_type_75k[['type', 'avg_days_listed']].to_string(index=False, header=False)}")
print()
top4_longest_days_listed_type_75k = vehicles_by_type_75k.nlargest(4, 'avg_days_listed')
print(f"Top 4 vehicle types with the longest average days listed ($75k and under):\n{top4_longest_days_listed_type_75k[['type', 'avg_days_listed']].to_string(index=False, header=False)}")
print()




Vehicle Listings ($75k and under) Summary by Type:
       type  count  avg_price  avg_odometer  percent_of_4wd  avg_days_listed
        bus     23    16620.3      114198.2             0.0             45.0
convertible    324    13709.0       87050.3             7.4             38.4
      coupe   1672    14660.3       79047.7             0.3             39.3
  hatchback    816     7036.3      111337.7            10.5             40.8
   mini-van    914     8328.6      126579.3             2.4             39.9
    offroad    176    14103.5      121938.6            72.0             39.8
     pickup   5414    16263.0      119746.4            54.2             39.5
      sedan   9176     7211.5      107743.1             2.9             39.4
        SUV   9414    11614.2      119443.5            53.7             40.0
      truck   9474    17025.2      124261.3            56.6             39.5
        van    443     9310.0      125290.3             3.7             40.6
      wagon   1189     91

Top 4 most listed vehicle types ($75k and under):
truck     9474
SUV       9414
sedan     9176
pickup    5414

Top 4 least listed vehicle types ($75k and under):
bus             23
offroad        176
convertible    324
van            443



Top 4 most expensive vehicle types by averge price ($75k and under):
 truck  17025.2
   bus  16620.3
pickup  16263.0
 coupe  14660.3

Top 4 least expensive vehicle types by average price ($75k and under):
hatchback  7036.3
    sedan  7211.5
 mini-van  8328.6
    wagon  9117.5

Top 4 vehicle types with the highest percentage of 4wd ($75k and under):
offroad 72.0
  truck 56.6
 pickup 54.2
    SUV 53.7

Top 4 vehicle types with the shortest average days listed ($75k and under):
convertible  38.4
      coupe  39.3
      sedan  39.4
     pickup  39.5

Top 4 vehicle types with the longest average days listed ($75k and under):
      bus  45.0
    wagon  40.9
hatchback  40.8
      van  40.6



In [25]:
# Grouping vehicles $75k and under by make and calculating the mean price, odometer reading, and days listed
vehicles_by_make_75k = df_75k.groupby('make', observed=True).agg(
    count=('make', 'size'),
    avg_price=('price', 'mean'),
    avg_odometer=('odometer', 'mean'),
    percent_of_4wd=('is_4wd', lambda x: (x > 0).mean() * 75),
    avg_days_listed=('days_listed', 'mean'),
).reset_index()
# Rounding the average price, odometer, and days listed to 1 decimal place
vehicles_by_make_75k[['avg_price', 'avg_odometer', 'percent_of_4wd', 'avg_days_listed']] = vehicles_by_make_75k[['avg_price', 'avg_odometer', 'percent_of_4wd', 'avg_days_listed']].round(1)
print(f"Vehicle Listings ($75k and under) Summary by Make:\n{vehicles_by_make_75k}")
print()

# Visualizing the number of vehicle listings by make
px.bar(
    vehicles_by_make_75k,
    x='make',
    y='count',
    labels={'make': "Vehicle Make", 'count': "Listings"},
    title='Vehicle Listings by Make ($75k and under)'
).show()
# Old plt graph
#vehicles_by_make_75k.plot(kind='bar', x='make', y='count', title='Number of Vehicle Listings by Make ($75k and under)')
#plt.xlabel('Vehicle Make')
#plt.legend().set_visible(False)
#plt.show()
# Displaying the top 4 most and least listed vehicle makes
top4_most_listed_type_75k = df_75k['make'].value_counts().head(4)
print(f"Top 4 most listed vehicle makes ($75k and under):\n{top4_most_listed_type_75k.to_string(header=False)}")
print()
top4_least_listed_type_75k = df_75k['make'].value_counts().tail(4).sort_values(ascending=True)
print(f"Top 4 least listed vehicle makes ($75k and under):\n{top4_least_listed_type_75k.to_string(header=False)}")
print()

# Distribution of vehicle prices $75k and under
px.histogram(
    df_75k,
    x='price',
    nbins=40,
    labels={'price': "Price ($)"},
    title='Distribution of Vehicle Prices ($75k and under)'
).update_yaxes(title_text="Listings").show()
# Old plt graph
#df_75k['price'].hist(bins=20,)
#plt.suptitle('Distribution of Vehicle Prices ($75k and under)')
#plt.xlabel('Price ($)')
#plt.ylabel('Frequency')
#plt.show()

# Visualizing the vehicle prices by make
px.box(
    df_75k,
    x='make',
    y='price',
    labels={'make':"Vehicle Make", 'price': "Price ($)"},
    title='Vehicle Prices by Make ($75k and under)'
).show()
# Old plt graph
#df_75k.boxplot(column='price', by='make', rot=45)
#plt.title('Vehicle Prices by Make ($75k and under)')
#plt.suptitle('')
#plt.xlabel('Vehicle Make')
#plt.ylabel('Price ($)')
#plt.show()
# Displaying the top 4 most and least expensive vehicle makes
top4_expensive_type_75k = vehicles_by_make_75k.nlargest(4, 'avg_price')
print(f"Top 4 most expensive vehicle makes by averge price ($75k and under):\n{top4_expensive_type_75k[['make', 'avg_price']].to_string(index=False, header=False)}")
print()
top4_least_expensive_type_75k = vehicles_by_make_75k.nsmallest(4, 'avg_price')
print(f"Top 4 least expensive vehicle makes by average price ($75k and under):\n{top4_least_expensive_type_75k[['make', 'avg_price']].to_string(index=False, header=False)}")
print()

# Displaying the top 4 vehicle makes with 4wd
top4_4wd_type_75k = vehicles_by_make_75k.nlargest(4, 'percent_of_4wd')
print(f"Top 4 vehicle makes with the highest percentage of 4wd ($75k and under):\n{top4_4wd_type_75k[['make', 'percent_of_4wd']].to_string(index=False, header=False)}")
print()

# Displaying the top 4 vehicle makes with the shorted and longest average days listed
top4_shortest_days_listed_type_75k = vehicles_by_make_75k.nsmallest(4, 'avg_days_listed')
print(f"Top 4 vehicle makes with the shortest average days listed ($75k and under):\n{top4_shortest_days_listed_type_75k[['make', 'avg_days_listed']].to_string(index=False, header=False)}")
print()
top4_longest_days_listed_type_75k = vehicles_by_make_75k.nlargest(4, 'avg_days_listed')
print(f"Top 4 vehicle makes with the longest average days listed ($75k and under):\n{top4_longest_days_listed_type_75k[['make', 'avg_days_listed']].to_string(index=False, header=False)}")
print()

# Grouping further by make and type
vehicles_by_maketype_75k = df_75k.groupby(['make', 'type'], observed=True).agg(
    count=('make', 'size'),
    avg_price=('price', 'mean'),
    avg_odometer=('odometer', 'mean'),
    percent_of_4wd=('is_4wd', lambda x: (x > 0).mean() * 75),
    avg_days_listed=('days_listed', 'mean')
).reset_index()
# Rounding the average price, odometer, and days listed to 1 decimal place
vehicles_by_maketype_75k[['avg_price', 'avg_odometer', 'percent_of_4wd', 'avg_days_listed']] = vehicles_by_maketype_75k[['avg_price', 'avg_odometer', 'percent_of_4wd', 'avg_days_listed']].round(1)
print(f"Vehicle Listings ($75k and under) Summary by Make and Type:\n{vehicles_by_maketype_75k}")
print()

px.bar(
    vehicles_by_maketype_75k,
    x='make',
    y='count',
    color='type',
    labels={'make': "Vehicle Make", 'count': "Listings"},
    title='Vehicle Listings by Make and Type ($75k and under)'
).show()

Vehicle Listings ($75k and under) Summary by Make:
          make  count  avg_price  avg_odometer  percent_of_4wd  \
0        acura    188     6345.8      143811.0             6.4   
1          bmw    210    10808.8      112532.3            67.9   
2        buick    217    11582.4      112857.6            36.6   
3     cadillac    241    17943.5      121287.0            59.1   
4    chevrolet   8085    14654.2      112334.5            40.7   
5     chrysler    642     8436.2      107655.2             5.5   
6        dodge    903     8656.8      116291.6            11.7   
7         ford   9641    12846.3      117532.8            39.5   
8          gmc   1815    15881.7      127466.6            56.4   
9        honda   2670     7529.6      126625.5            16.8   
10     hyundai    898     7331.4      103698.0             8.7   
11        jeep   2402    13583.7      111480.3            67.5   
12         kia    444     8593.2       94419.7            17.9   
13      nissan   2382    

Top 4 most listed vehicle makes ($75k and under):
ford         9641
chevrolet    8085
toyota       4149
honda        2670

Top 4 least listed vehicle makes ($75k and under):
acura       188
bmw         210
buick       217
cadillac    241



Top 4 most expensive vehicle makes by averge price ($75k and under):
      ram  18893.3
 cadillac  17943.5
      gmc  15881.7
chevrolet  14654.2

Top 4 least expensive vehicle makes by average price ($75k and under):
     acura  6345.8
   hyundai  7331.4
volkswagen  7414.8
     honda  7529.6

Top 4 vehicle makes with the highest percentage of 4wd ($75k and under):
  subaru 73.3
     bmw 67.9
    jeep 67.5
cadillac 59.1

Top 4 vehicle makes with the shortest average days listed ($75k and under):
  chrysler  38.4
   hyundai  38.5
    nissan  38.6
volkswagen  39.2

Top 4 vehicle makes with the longest average days listed ($75k and under):
     bmw  42.4
     kia  42.1
cadillac  41.5
     gmc  41.0

Vehicle Listings ($75k and under) Summary by Make and Type:
           make       type  count  avg_price  avg_odometer  percent_of_4wd  \
0         acura      sedan    186     6360.8      143991.8             6.5   
1         acura        SUV      2     4950.0      127000.0             0.0   
2

In [10]:
# Drawing a pie chart to visualize the distribution of transmission types
px.pie(df_75k, names='transmission', title='Distribution of Transmission Types', hole=0.3).show()
# Analyzing vehicle transmission types
automatic = df_75k['transmission'].value_counts().get('automatic', 0)
manual = df_75k['transmission'].value_counts().get('manual', 0)
other_trans = df_75k['transmission'].value_counts().get('other', 0)
print(f"Number of vehicles with automatic transmission: {automatic}")
print(f"Number of vehicles with manual transmission: {manual}")
print(f"Number of vehicles with unknown transmission: {other_trans}")
# Old plt graph
#transmission_counts = df_75k['transmission'].value_counts()
#plt.figure(figsize=(8, 6))
#transmission_counts.plot(kind='pie', autopct='%1.1f%%', startangle=90, ylabel='')
#plt.title('Distribution of Transmission Types')
#plt.show()
print()

# Getting value counts for the fuel type column
fuelcount = df_75k['fuel'].value_counts()
# Keeping only the top 2 categories, sum the rest as 'Other'
top2 = fuelcount.head(2)
other = fuelcount[2:].sum()
pie_data = pd.concat([top2, pd.Series({'Other': other})])

# Plotting the fuel type distribution pie chart
px.pie(pie_data, names=pie_data.index, values=pie_data.values, title='Distribution of Fuel Types', hole=0.3).show()
# Analyzing fuel types
gas = df_75k['fuel'].value_counts().get('gas', 0)
diesel = df_75k['fuel'].value_counts().get('diesel', 0)
hybrid = df_75k['fuel'].value_counts().get('hybrid', 0)
other_fuel = df_75k['fuel'].value_counts().get('other', 0)
electric = df_75k['fuel'].value_counts().get('electric', 0)
print(f"Number of vehicles with gas fuel: {gas}")
print(f"Number of vehicles with diesel fuel: {diesel}")
print(f"Number of vehicles with hybrid fuel: {hybrid}")
print(f"Number of vehicles with other fuel: {other_fuel}")
print(f"Number of vehicles with electric fuel: {electric}")
# Old plt graph
#plt.figure(figsize=(6, 6))
#pie_data.plot(kind='pie', autopct='%1.1f%%', startangle=90, ylabel='')
#plt.title('Distribution of Fuel Types')
#plt.show()


Number of vehicles with automatic transmission: 35755
Number of vehicles with manual transmission: 2096
Number of vehicles with unknown transmission: 1184



Number of vehicles with gas fuel: 35799
Number of vehicles with diesel fuel: 2843
Number of vehicles with hybrid fuel: 315
Number of vehicles with other fuel: 74
Number of vehicles with electric fuel: 4
